In [1]:
import numpy as np
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots

In [2]:
data_desc={
    'model': ['ANI-1ccx MACE', 'MACE-OFF23',  's66x8 MACE'],
    'paths': ['/Users/dominicwelti/Documents/Master_Thesis_Data_Set/Graphite/ANI-1ccx/grid_search.pkl', '/Users/dominicwelti/Documents/Master_Thesis_Data_Set/Graphite/mace-off23_large_graphite_grid_search.pkl', '/Users/dominicwelti/Documents/Master_Thesis_Data_Set/Graphite/mace_s66x8_graphite.pkl']
}

In [3]:
df_lst=[]
for model, path in zip(data_desc['model'], data_desc['paths']):
    df=pd.read_pickle(path)
    df['Model']=model
    df_lst.append(df)
    print(model,path)

df=pd.concat(df_lst)

ANI-1ccx MACE /Users/dominicwelti/Documents/Master_Thesis_Data_Set/Graphite/ANI-1ccx/grid_search.pkl
MACE-OFF23 /Users/dominicwelti/Documents/Master_Thesis_Data_Set/Graphite/mace-off23_large_graphite_grid_search.pkl
s66x8 MACE /Users/dominicwelti/Documents/Master_Thesis_Data_Set/Graphite/mace_s66x8_graphite.pkl


In [11]:
def subset_factors(df):
    df['Total energy']=pd.to_numeric(df['Total energy'])
    df=df.query('1.5>`Factor a`>0.9 & 1.5>`Factor c`>0.9')#& `Total energy`<0'
    df.reset_index(drop=True, inplace=True)
    return df

In [12]:
df=subset_factors(df)

In [6]:
def prune(df:pd.DataFrame,precision:float=0.05):
    '''Decrease mesh density to enable plotting of larger area.'''
    sec_a=df['Parameter a'][0]
    sec_c=df['Parameter c'][0]
    drop_lst=[]
    for i, (par_a, par_c) in enumerate(zip(df['Parameter a'],df['Parameter c'])):
        if (sec_a+precision)>par_a>(sec_a-precision):
            if (sec_c+precision)>par_c>(sec_c-precision):
                drop_lst.append(i)
            else:
                sec_c=par_c
        else:
            sec_a=par_a

    return df.drop(index=drop_lst)

In [7]:
df=prune(df)

In [13]:
fig = make_subplots(rows=1,
                    cols=len(data_desc['model']),
                    specs=[len(data_desc['model'])*[{'type': 'scene'}]],
                    subplot_titles=df['Model'].unique()
                    )

for i, model in enumerate(df['Model'].unique()):
    df_sub=df.query(f'Model=="{model}"')
    min_pt = df_sub.iloc[df_sub['Total energy'].argmin()] #data point containing minimum energy
    #df_sub=df_sub.query(f"({min_pt['Parameter a']+1}>`Parameter a`>{min_pt['Parameter a']-1}) & ({min_pt['Parameter c']+2}>`Parameter c`>{min_pt['Parameter c']-2}) & `Total energy`<{-4000}")
    df_sub=df_sub.query(f"`Total energy`<{-4000}")
    fig.add_trace(
        go.Mesh3d(x=df_sub['Parameter a'], y=df_sub['Parameter c'],z=df_sub['Total energy'],
                  opacity=0.8,
                  name=model),
        row=1,
        col=i+1
    )
    fig.add_trace(
        go.Scatter3d(x=[min_pt['Parameter a']],
                    y=[min_pt['Parameter c']],
                    z=[min_pt['Total energy']],
                    marker = dict(
                        size=10,
                        color='red',
                        opacity=0.5),
                    name='Energy minima'
        ),
        row=1,
        col=i+1
    )
    
    fig.update_scenes(
        zaxis=dict(title='Total energy [eV]'), 
        yaxis=dict(title='Lattice parameter c [Å]'),
        xaxis=dict(title='Lattice parameter a [Å]')
    )

fig.update_layout(title='Grid search for potentials on bulk graphite',
                  showlegend=False
)

In [10]:
fig.write_html('/Users/dominicwelti/Documents/Master_Thesis_Data_Set/Graphite/gridsearch.html')